# Isochrones: tests, overlays, isolignes, masques

## Table des matières

* [*** 1. Exploration des données issues des requêtes journeys de Navitia pour essayer de recréer un isochrone***](#explore_data)

    * [1.1. Preparation](#prepa)
    
    * [1.2. Utilisation de la librairie développée spécifiquement](#ut_lib)
    
        * [*1.2.1. Lancement des premiers calculs*](#prem_calcs)
    
        * [*1.2.2.Importer les lignes et les points du réseau pour les cartographier*](#carto_reseau)
    
    * [1.3. Exploration des résultats: cartographie de tous les chemins minimaux](#explo_ch_min)
    
    * [1.4. Exploration des résultats: cartographie des durées et des distances à pied](#explo_carto)

* [***2. Etude de variations de représentations***](#var_repr)

    * [2.1 Différentes manières de représenter les isochrones](#diff_man_iso)

        * [*2.1.1. Les buffers autour des stations et leur union*](#buff_stations)

    * [2.2Isochrones et réseau viaire: isolignes "*bufferisées*" et opérations spatiales (*difference, union, intersection, symmetric_difference*)](#iso_viaire)

        * [*2.2.1. Récupérer un réseau viaire sous la forme d'un graphe*](#recup_reseau)

        * [*2.2.2. Des fonctions pour mesurer des temps de calculs*](#fonc_calc)

        * [*2.2.3. Import des modules et lancement du programme à partir du fichier de paramètres*](#lanc_prog)

        * [*2.2.4. Récupération des résultats et formatage pour les glyphs *multi_polygons* Bokeh*](#format_bokeh)

        * [*2.2.4. Cartographie des résultats*](#bokeh_map)

        * [*2.2.5. Export en svg*](#export_svg)

* [***3. Couches et masques (*en cours*)***](#layer_mask)



<a id="explore_data"></a>
## 1. Exploration des données issues des requêtes "*[journeys](https://doc.navitia.io/#journeys)*" de Navitia pour essayer de recréer un isochrone

On se base sur l'API de Navitia pour obtenir les points qui permettent de composer les isochrones.

Pour les besoins de ce test (*dans cette partie 1*), nous allons récupérer, à partir d'une requête sur un noeud d'origine, les noeuds et le temps nécessaire pour les atteindre avec les paramètres suivants (*cf. fichier de paramètres*):
* *durée maximale*: **20 minutes**
* *adresse de départ*: **"90, Boulevard Saint-Germain, 75005, France"**
* *date*: **2018-12-06** (*yyyy-mm-dd*)
* *heure*: **08:00**
* *API*: **Navitia** ([journeys](https://doc.navitia.io/#journeys))

Il s'agit d'utiliser la requête *journeys* de Navitia pour mesurer l'accessibilité aux différentes stations de transports en commun en partant d'une origine en vue:
* d'explorer les résultats
* de recréer un isochrone similaire à celui issu des requêtes "isochrone" de Navitia
Tout ceci afin de voir comment partir de cette base pour essayer des alternatives, des croisements, des superpositions, ... 

<a id="prepa"></a>
### 1.1 Préparation
Tout d'abord, on importe le chemin du module dans le path

In [2]:
# Add module to path
import os
import sys

add_path = os.getcwd().replace('experiments', '')
sys.path.append(add_path)

<a id="ut_lib"></a>
### 1.2 Utilisation de la librairie développée spécifiquement
Ensuite on lance le module avec les paramètres (*présents dans le fichier de paramètre*). Nous récupérons tous les plus courts chemins (*modes, stations, durées, ...*) du noeuds d'origine vers chaque noeud retourné par la requête initiale (*qui donne tous les noeuds permettant de créer un isochrone avec une durée maximale de X minutes*). 

<a id="prem_calcs"></a>
#### 1.2.1 Lancement des premiers calculs

In [4]:
from dotenv import load_dotenv
import docopt
import json
from pathlib import Path
from csv_to_json import csv_to_json
from isos_and_intersections import GetIso

param_csv = os.path.join(add_path, "params/test_journeys.csv")
param_json = os.path.join(add_path, "params/test_journeys.json")
places_cache = os.path.join(add_path, "params/places_cache.json")

#Parameters
env_path = Path(add_path) / '.env'
load_dotenv(dotenv_path=env_path)
TOKEN = os.getenv("NAVITIA_TOKEN")

columns_with_array_of_str = [
    "addresses",
    "excluded_modes",
    "durations"
    ]

#JSON INPUT
json_file = csv_to_json(param_csv, param_json, ";", columns_with_array_of_str)

gdf_global = GetIso(param_json, places_cache, api="navitia", token=TOKEN).get_all_isos()

URL https://api.navitia.io/v1/coverage/fr-idf/journeys?from=2.3447555;48.8511485&datetime=2018-12-06T08:00&max_duration=1200


C:\Users\thomas\Documents\code\iso\app_iso\code\osmnx_based_functions.py:201: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  gdf_lines.drop_duplicates(subset=["source","target"],inplace=True)
C:\Users\thomas\Documents\code\iso\app_iso\code\osmnx_based_functions.py:202: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  gdf_lines['xs'] = gdf_lines.apply(getLineCoords, geom='line', coord_type='x', axis=1)
C:\Users\thomas\Documents\code\iso\app_iso\code\osmnx_based_functions.py:203: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_i

polys 00:00:06:589
Overlays 00:01:00:708


<a id="carto_reseau"></a>
#### 1.2.2 Importer les lignes et les points du réseau pour les cartographier

On importe des fichiers GeoJSON (*calculés au préalable et stockés*) d'une partie des lignes et des stations de transports en commun pour les cartographier et avoir un premier aperçu de ce type de données. 

In [5]:
import geopandas as gpd
import geojson

from geo_functions import gdf_to_geojson, geosource

#Filter: no "NR"
lines = gdf_global["journeys_details_lines"]
pts = gdf_global["journeys_details_pts"]
# filter_lines = lines.loc[lines["mode"] != "NR"]
# filter_pts = pts.loc[pts["mode"] != "NR"]

if lines is None:
    source_lines = geosource("lines_test.geojson")
    source_pts = geosource("points_test.geojson")
else:
    #Save to geojson
    lines.to_file("lines_test.geojson", driver="GeoJSON")
    pts.to_file("points_test.geojson", driver="GeoJSON")

    #Transform gdf to geojson
    columns_lines = list(lines.columns)
    columns_pts = list(pts.columns)
    geo_source_lines = gdf_to_geojson(lines, columns_lines, "epsg:3857")
    geo_source_pts = gdf_to_geojson(pts, columns_pts, "epsg:3857")
    source_lines = GeoJSONDataSource(geojson=geo_source_lines)
    source_pts = GeoJSONDataSource(geojson=geo_source_pts)

<a id="explo_ch_min"></a>
### 1.3 Exploration des résultats: cartographie de tous les chemins minimaux
On cartographie les lignes et les noeuds (*colorés en fonction du mode*) qui représentent tous les chemins minimaux entre le noeud d'origine et les X noeuds du réseau atteignables dans le temps donné. 

In [6]:
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.tile_providers import STAMEN_TONER_BACKGROUND
from bokeh.models import GeoJSONDataSource, ColumnDataSource, CategoricalColorMapper
from bokeh.palettes import Colorblind8 as cb
from bokeh.transform import factor_cmap
import json
from pyproj import Proj, transform

output_notebook()

#Set origin
lat = 2.3467922
lng = 48.8621487
inProj = Proj(init='epsg:4326')
outProj = Proj(init='epsg:3857')
lat,lng = transform(inProj,outProj,lat,lng)
data_ori = {
    "x":[lat],
    "y":[lng],
    "name":["Origin"]
}

ori = ColumnDataSource(data_ori)

# Set colors by mode
modes = ['Métro', 'RER', 'Bus', 'Tramway', 'NR']
palette = [cb[0], cb[1], cb[2], cb[4], 'grey']

color_mapper = CategoricalColorMapper(factors=modes, palette=palette)

# Set the tooltips for hover
TOOLTIPS = [
    ("index", "$index"),
    ("mode", "@mode"),
    ("name", "@name"),
    ("direction", "@direction")
]

p = figure(tooltips=TOOLTIPS)
p.width = 800
p.add_tile(STAMEN_TONER_BACKGROUND, alpha=0.2)


p.multi_line(
    xs='xs',
    ys='ys',
    line_width=2,
    line_color= {'field': 'mode', 'transform': color_mapper},
    line_alpha=0.5,
    source=source_lines,
    legend="Lines"
)


p.circle(
    x='x',
    y='y',
    size = 5,
    color = {'field': 'mode', 'transform': color_mapper},
    source=source_pts,
    legend="Nodes"
)

#Add ori
p.triangle(
    x="x",
    y="y",
    size=20,
    color="red",
    alpha=0.5,
    source=ori,
    legend="Origin"
)

p.legend.click_policy="hide"

#Add a workaround to get a custom legend with geojson
#See https://github.com/bokeh/bokeh/issues/5904#issuecomment-296219499
for factor, color in zip(color_mapper.factors, color_mapper.palette):
    p.square(x=[], y=[], fill_color=color, size=10, line_alpha=0.0, legend=factor)

show(p)

Loading BokehJS ...

<a id="explo_carto"></a>
### 1.4 Exploration des résultats: cartographie des durées et des distances à pied
On peut cartographier les noeuds du réseau issu de la requête principale:
* *avec la durée nécessaire pour les atteindre depuis le noeud d'origine*) => Carte "Duration from origin point"
* *avec le potiential de marche à pied depuis chaque noeud (en fonction du temps restant)*) => Carte "Walkable distance from nodes"

> Les 2 cartes sont liées (le pan et le zoom sont synchronisés sur les 2 cartes). 

In [7]:
from bokeh.palettes import Viridis256, Magma11, RdYlBu11, Greens9, Inferno256
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.tile_providers import STAMEN_TONER_BACKGROUND
from bokeh.models import GeoJSONDataSource, ColumnDataSource, LinearColorMapper, LogTicker, ColorBar
from bokeh.layouts import gridplot
import json

from geo_functions import gdf_to_geojson

output_notebook()

TOOLTIPS = [
    ("name", "@to_name"),
    ("duration", "@duration"),
    ("walkable_distance", "@walkable_distance")
]

TOOLS = "pan,box_zoom,wheel_zoom,box_select,lasso_select,save,reset,hover"

#####################
#DURATION FROM ORIGIN
#####################
#Create color mapper
color_mapper = LinearColorMapper(palette=Viridis256)

#Prepare the data
columns_nodes = list(gdf_global["journeys_points"].columns)
nodes = gdf_to_geojson(gdf_global["journeys_points"], columns_nodes, "epsg:3857")

p = figure(
    title="Duration from origin point",
    tooltips=TOOLTIPS, 
    tools=TOOLS
)
p.width = 450
p.add_tile(STAMEN_TONER_BACKGROUND, alpha=0.2)

source_circles = GeoJSONDataSource(geojson=nodes)
p.circle(
    x='x',
    y='y',
    fill_color={'field': 'duration', 'transform': color_mapper},
    fill_alpha=0.5,
    line_color="white",
    line_alpha=0.0,
    size=10,
    source=source_circles
)


color_bar = ColorBar(color_mapper=color_mapper, ticker=LogTicker(),
                     label_standoff=120, border_line_color=None, location=(0,0))
p.add_layout(color_bar, 'right')
############################################

#####################
#WALKABLE DISTANCE
#####################
#Create color mapper
color_mapper = LinearColorMapper(palette=Viridis256)

p2 = figure(
    title="Walkable distance from nodes (meters)",
    x_range=p.x_range, 
    y_range=p.y_range,
    tooltips=TOOLTIPS,
    tools=TOOLS
)
p2.width = 450
p2.add_tile(STAMEN_TONER_BACKGROUND, alpha=0.2)

p2.circle(
    x='x',
    y='y',
    fill_color={'field': 'walkable_distance', 'transform': color_mapper},
    fill_alpha=0.5,
    line_color="white",
    line_alpha=0.0,
    size=10,
    source=source_circles
)


color_bar = ColorBar(color_mapper=color_mapper, ticker=LogTicker(),
                     label_standoff=120, border_line_color=None, location=(0,0))
p2.add_layout(color_bar, 'right')
############################################

grid = gridplot(
    [
        [p,p2]
    ],
    toolbar_location='right'
     )


show(grid)

Loading BokehJS ...

<a id="var_repr"></a>
## 2. Etude de variations de représentations
<a id="diff_man_iso"></a>
### 2.1 Différentes manières de représenter les isochrones
<a id="buff_stations"></a>
#### 2.1.1 Les buffers autour des stations et leur union
On essaie de reproduire la méthode employée par l'API Navitia:
* 1) temps de marche à pied disponible => temps maximum de déplacement - temps de déplacement
* 2) distance de marche à pied => vitesse marche * temps de marche disponible
* 3) buffer de cette distance pour chaque noeud 
* 4) union des buffers

In [8]:
import numpy as np

def buffering(point, distance):
    return point.buffer(distance, resolution=16)

pts = gdf_global["journeys_points"]
#Prepare the data (get buffer from walkable distance)
pts["buffer"] = np.vectorize(buffering)(pts["geometry"], pts["walkable_distance"])
pts = pts.rename(columns={'geometry': 'pts'})
pts = pts.rename(columns={'buffer': 'geometry'}).set_geometry('geometry')

In [9]:
from shapely.ops import cascaded_union

#########
# BUFFERS
#########
#Create color mapper
color_mapper = LinearColorMapper(palette=Viridis256)

#Prepare the data
columns_pts = list(pts.columns)
nodes = gdf_to_geojson(pts, columns_pts, "epsg:3857")

p = figure(
    title="Buffers",
    tooltips=TOOLTIPS, 
    tools=TOOLS
)
p.width = 450
p.add_tile(STAMEN_TONER_BACKGROUND, alpha=0.2)

source_pts = GeoJSONDataSource(geojson=nodes)
p.patches(
    xs='xs',
    ys='ys',
    fill_color={'field': 'duration', 'transform': color_mapper},
    fill_alpha=0.5,
    line_color="white",
    line_alpha=0.0,
    source=source_pts
)


########
# UNION
########

#Prepare the data
columns_pts = list(pts.columns)
nodes = gdf_to_geojson(pts, columns_pts, "epsg:3857")

p2 = figure(
    title="Union of buffers",
    tooltips=TOOLTIPS, 
    tools=TOOLS,
    x_range=p.x_range, 
    y_range=p.y_range,
)
p2.width = 450
p2.add_tile(STAMEN_TONER_BACKGROUND, alpha=0.2)

#Union of buffers
one_buffer = gpd.GeoSeries(cascaded_union(pts["geometry"]))
buffer = gpd.GeoDataFrame()
buffer["geometry"] = one_buffer
buffer_json = gdf_to_geojson(buffer, [], "epsg:3857")

source_buffer = GeoJSONDataSource(geojson=buffer_json)
p2.patches(
    xs='xs',
    ys='ys',
    fill_color="green",
    fill_alpha=0.5,
    line_color="white",
    line_alpha=0.0,
    source=source_buffer
)


grid = gridplot(
    [
        [p,p2]
    ],
    toolbar_location='right'
     )

show(grid)

Nous avons reproduit la méthode employé par Navitia pour créer des isochrones en partant de la requête *journeys*. Nous allons maintenant nous pencher sur les possibilités de représentations avec le réseau viaire (*qu'on utilisera avec une vitesse de marche à pied*). 

<a id="iso_viaire"></a>
### 2.2 Isochrones et réseau viaire: isolignes "*bufferisées*" et opérations spatiales (*difference, union, intersection, symmetric_difference*)

<a id="recup_reseau"></a>
#### 2.2.1 Récupérer un réseau viaire sous la forme d'un graphe 

> Avertissement: si vous souhaitez tester le code ci-dessous, veillez à ne pas mettre une distance trop importante. Pour donner un exemple, la distance entrée initialement est de 50 000 mètres et cela prend entre 40 et 50 minutes pour récupérer le graphe. C'est pour cette raison que nous écrivons le graphe sous la forme de 2 fichiers JSON (*noeuds et arcs*). 

In [ ]:
# Add module to path
import os
import sys
import time
import json
import osmnx as ox

add_path = os.getcwd().replace('experiments', '')
sys.path.append(add_path)

from osmnx_based_functions import graph_with_time


edges_path = os.path.join(add_path, "graphs\Paris_50km_edges.json")
nodes_path = os.path.join(add_path, "graphs\Paris_50km_nodes.json")

point = 2.3467922,48.8621487

distance = 50000
G = graph_with_time(point, distance, edges_path, nodes_path, epsg={"init":"epsg:3857"})


<a id="fonc_calc"></a>
#### 2.2.2 Des fonctions pour mesurer des temps de calculs

In [3]:
import time

def seconds_to_time(seconds, option="all"): 
    milliseconds = int(round(seconds * 1000))
    s, ms = divmod(milliseconds, 1000)
    m, s = divmod(s, 60)
    h, m = divmod(m, 60)
    time_format = "%02d:%02d:%02d:%02d" % (h, m, s, ms)
    
    if option == "all":
        return time_format, milliseconds
    elif option == "ms":
        return milliseconds
    elif option == "format":
        return time_format
    

def time_profile(start, option="all"):
    end = time.time()
    seconds = seconds_to_time(end - start, option=option)
    
    return seconds

<a id="lanc_prog"></a>
#### 2.2.3 Import des modules et lancement du programme à partir du fichier de paramètres

In [6]:
# Add module to path
import os
import sys
import time
import json

add_path = os.getcwd().replace('experiments', '')
sys.path.append(add_path)

from dotenv import load_dotenv
import docopt
import json
from pathlib import Path
from csv_to_json import csv_to_json
from isos_and_intersections import GetIso

param_csv = os.path.join(add_path, "params/test_journeys.csv")
param_json = os.path.join(add_path, "params/test_journeys.json")
places_cache = os.path.join(add_path, "params/places_cache.json")

#Parameters
env_path = Path(add_path) / '.env'
load_dotenv(dotenv_path=env_path)
TOKEN = os.getenv("NAVITIA_TOKEN")

columns_with_array_of_str = [
    "addresses",
    "excluded_modes",
    "durations"
    ]

#JSON INPUT
json_file = csv_to_json(param_csv, param_json, ";", columns_with_array_of_str)

start = time.time()
gdf_global = GetIso(param_json, places_cache, api="navitia", token=TOKEN).get_all_isos()
print ("TOTAL GDF_GLOBAL",time_profile(start, option = "format"))

URL https://api.navitia.io/v1/coverage/fr-idf/journeys?from=2.3447555;48.8511485&datetime=2019-01-17T08:00&max_duration=1200


C:\Users\thomas\Documents\code\iso\app_iso\code\osmnx_based_functions.py:201: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  gdf_lines.drop_duplicates(subset=["source","target"],inplace=True)
C:\Users\thomas\Documents\code\iso\app_iso\code\osmnx_based_functions.py:202: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  gdf_lines['xs'] = gdf_lines.apply(getLineCoords, geom='line', coord_type='x', axis=1)
C:\Users\thomas\Documents\code\iso\app_iso\code\osmnx_based_functions.py:203: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_i

polys 00:00:07:63
Overlays 00:01:02:731
TOTAL GDF_GLOBAL 00:01:41:58


<a id="format_bokeh"></a>
#### 2.2.4 Récupération des résultats et formatage pour les glyphs *multi_polygons* Bokeh

In [7]:
from shapely.ops import cascaded_union
from geo_functions import multi_gdf_to_multi_bokeh as mbokeh

id_ = "all_08h00_Chatelet"
address = "90, Boulevard Saint-Germain, 75005, France"
duration = 20
key = id_, address, duration

lines = gdf_global["isolines"][key]["gdf_lines"]
polys_union = gdf_global["isolines"][key]["polys_union"]
sym_diff = gdf_global["isolines"][key]["symmetric_difference"]
difference = gdf_global["isolines"][key]["difference"]
intersection = gdf_global["isolines"][key]["intersection"]
union = gdf_global["isolines"][key]["union"]
isochrones = gdf_global["isolines"][key]["isochrones"]

data = {
    "union":mbokeh(union),
    "difference":mbokeh(difference),
    "lines_buffer":mbokeh(polys_union),
    "sym_diff":mbokeh(sym_diff),
    "intersection": mbokeh(intersection),
    "isochrones": mbokeh(isochrones)
}


<a id="bokeh_map"></a>
#### 2.2.4 Cartographie des résultats
> * ***Union*** => Union des isochrones et des isolignes bufferisées
> * ***Difference*** => Difference entre les isochrones et les isolignes bufferisées
> * ***Lines_buffer*** => Lignes bufferisées
> * ***Symm_diff*** => Difference symétrique entre les isochrones et les isolignes bufferisées
> * ***Intersection*** => Intersection entre les isochrones et les isolignes bufferisées
> * ***Isochrones*** => Isochrones

> *Pour plus d'informations sur les méthodes d'overlays, voir la [documentation de GeoPandas](http://geopandas.org/set_operations.html)*

In [14]:
add_path = os.getcwd().replace('experiments', '')
sys.path.append(add_path)

import geopandas as gpd
import geojson
from bokeh.plotting import figure, show
from bokeh.palettes import Viridis256, Magma11, RdYlBu11, Greens9, Inferno256, Viridis6
from bokeh.io import output_notebook
from bokeh.tile_providers import STAMEN_TONER_BACKGROUND
from bokeh.models import GeoJSONDataSource, ColumnDataSource, CategoricalColorMapper, LinearColorMapper
from bokeh.palettes import Colorblind8 as cb
from bokeh.transform import factor_cmap
import json
from pyproj import Proj, transform

output_notebook()


#Prepare the Bokeh figure
# color_mapper = LinearColorMapper(palette=Viridis4)
p = figure(
    title="Overlays"
)

p.width = 800
p.add_tile(STAMEN_TONER_BACKGROUND, alpha=0.2)


#Set origin
lat = 2.34472
lng = 48.85103
inProj = Proj(init='epsg:4326')
outProj = Proj(init='epsg:3857')
lat,lng = transform(inProj,outProj,lat,lng)
data_ori = {
    "x":[lat],
    "y":[lng],
    "name":["Origin"]
}

ori = ColumnDataSource(data_ori)

#Prepare overlays
i=0
for name,value in data.items():
    p.multi_polygons(
    xs=value['xs'],
    ys=value['ys'],
    color=Viridis6[i],
    alpha=0.5,
    legend=name
    )
    i+=1

#Add ori
p.triangle(
    x="x",
    y="y",
    size=20,
    color="red",
    alpha=0.5,
    source=ori,
    legend="Origin"
)

p.legend.click_policy="hide"


show(p)

Loading BokehJS ...

<a id="export_svg"></a>
#### 2.2.5 Export en svg

In [ ]:
from bokeh.io import export_svgs

p.output_backend = "svg"
export_svgs(p, filename="figure.svg")

<a id="layer_mask"></a>
## 3. Couches et masques (*en cours*)

Il s'agit ici de procéder à des tests de superposition de différentes couches et d'utilisation de masques. 

In [ ]:
# Add module to path
import os
import sys

add_path = os.getcwd().replace('experiments', '')
sys.path.append(add_path)

from spatial_cutting import get_transit_network

